Polaris Injector Calcs

In this program we will calculate all the parameters necessary to design an unlike impinging triplet injector. 

In [62]:
import numpy as np
import matplotlib.pyplot as plt
import math

First off, we need to know the mass flow rates of the oxidizer (nitrous oxide) and fuel (ethanol). Our total mass flow rate is 1.3 kg/s. However, our fuel to oxidizer ratio is 1:4.5, so we need a lot more oxidizer mass flow rate than fuel. We will distribute the flow rate by having two orifices for oxidizer and one orifice for fuel per triplet group. To obtain the ratios of mass flow rates, we can simply multiply the total mass flow by each ratio, accounting for the fact that there are 3 orifices per group and 5 groups in total.

In [63]:
mdot_nitrous_inner_total = 1.3 * (4.5/5.5) / 2
mdot_nitrous_middle_total = 1.3 * (4.5/5.5) / 2
mdot_ethanol_total = 1.3 * (1/5.5)

mdot_nitrous_inner = mdot_nitrous_inner_total / 5
mdot_nitrous_middle = mdot_nitrous_middle_total / 5
mdot_ethanol = mdot_ethanol_total / 5
mdot_nitrous_inner_total
print("mdot_ox: ", mdot_nitrous_inner)
print("mdot_ethanol: ", mdot_ethanol)

mdot_ox:  0.10636363636363637
mdot_ethanol:  0.04727272727272728


Here are some other necessary parameters:
c_d is the discharge coefficient, which was calculated in a MATLAB program run by Alex. It is the predicted ratio of actual discharge of mass at the end of the nozzle to ideal discharge of mass at the end of the nozzle.

rho_ethanol is the density of ethanol (789 kg/m^3).

rho_nitrous is the density of nitrous oxide (817 kg/m^3).
pressure_chamber is the stagnation pressure of the chamber converted from 520 psi to Pa. 

delta_pressure_injector is the pressure drop across the injector in Pa (converted from 100 psi), should be 15-20% of the chamber pressure.

pressure_fuel_inlet is the pressure in the fuel manifold.

pressure_oxidizer_inlet is the pressure in the oxidizer manifold.

d_ox is the diameter of the oxidier holes in inches.

d_fuel is the diameter of the fuel holes in inches.

v_nitrous is the exit velocity from the oxidizer orifices. Calculated via Bernoulli's principle

v_ethanol is the exit velocity from the fuel orifices. Calculated via Bernoulli's principle.

In [64]:
c_d = 0.41
rho_ethanol = 789
rho_nitrous = 817
pressure_chamber = 460*6895
delta_pressure_injector = 97*6895
pressure_fuel_inlet = delta_pressure_injector + pressure_chamber
pressure_oxidizer_inlet = delta_pressure_injector + pressure_chamber
d_ox = 7/64
d_fuel = 1/16
v_nitrous = np.sqrt((2*delta_pressure_injector)/rho_nitrous)
v_ethanol = np.sqrt((2*delta_pressure_injector)/rho_ethanol)
print("v_nitrous: ", v_nitrous)
print("v_ethanol: ", v_ethanol)

v_nitrous:  40.4628968566491
v_ethanol:  41.17461041052858


Now let's define some helper functions to convert angles from deg to rad and vice versa.

In [65]:
def deg_to_rad(angle):
    """ Converts angle from deg to rad."""
    return angle*np.pi/180

def rad_to_deg(angle):
    """ Converts angle from rad to deg."""
    return angle*180/np.pi

Now that we have the necessary base parameters, we will calculate the optimal angles from the vertical for each orifice in a triplet. To do this we can use a conservation of momentum equation. In this conservation of momentum equation, we choose an angle beta of 10 degrees for the resulting momentum stream to mitigate oxidiizer accumulation on the chamber walls.

In [66]:
beta = deg_to_rad(10)

For this geometry, the horizontal component of the fuel and middle nitrous orifice are pointing radially inward. Only the inner oxidizer is has a horizontal component pointing radially outward. We implement this by adding a direction (minus or plus) on each momentum component. See the CAD for more detail.

The general formula for the optimal angles for the three orifices is derived by using conservation of momentum on the three impinging streams and isolating tan(beta). This equation is very messy and unfortunately has three variables. However, we can use the relation provided in a JPL paper, which stated that the optimal included angle of a doublet is 60 degrees. We can translate this to a triplet design by saying that the included angle between the fuel and the inner oxidizer orifice should be 60 degrees. Therefore, we can define the angle of the fuel orifice in terms of the inner oxidizer orifice, reducing our equation to two variables.

Next, we reorganize the equation so that we can solve for one angle in terms of another angle and define some intermediate parameters (b and c) to make the final equation more concise.

In [67]:
def calculate_theta_nitrous_middle(asserted_inner_angle, beta=beta):
    """
    Given a desired angle for the inner nitrous orifice (deg) and angle
    of resultant spray after impingement (beta), returns ideal angle
    for middle nitrous orifice (deg). All angles relative to vertical.
    """
    theta_nitrous_inner = deg_to_rad(asserted_inner_angle) # radians
    b = np.tan(beta)
    c = ((b * mdot_ethanol * v_ethanol * np.cos(deg_to_rad(60)-theta_nitrous_inner) 
        + b * mdot_nitrous_inner * v_nitrous * np.cos(theta_nitrous_inner) 
        - mdot_ethanol * v_ethanol * np.sin(deg_to_rad(60)-theta_nitrous_inner) 
        + mdot_nitrous_inner * v_nitrous * np.sin(theta_nitrous_inner))
        /(mdot_nitrous_middle * v_nitrous))
    theta_nitrous_middle = rad_to_deg(2*np.arctan((np.sqrt(b**2 - c**2 + 1)-1)/(b-c)))
    return theta_nitrous_middle

# suppose we want 14 deg inner
theta_nitrous_inner = int(input("Please enter an angle for the inner oxidizer orifice: "))
theta_nitrous_middle = calculate_theta_nitrous_middle(theta_nitrous_inner)
theta_fuel = 60-theta_nitrous_inner
print("theta_nitrous_inner: ", theta_nitrous_inner)
print("theta_nitrous_middle: ", theta_nitrous_middle)
print("theta_fuel: ", theta_fuel)

Please enter an angle for the inner oxidizer orifice: 14
theta_nitrous_inner:  14
theta_nitrous_middle:  18.100146575234053
theta_fuel:  46


Next, we want to calculate the distance of the three orifices that will allow the three streams to meet at a single point for a given impingement distance. We define the impingement distance to be 5 times the average the of diameters of the three orifices. From there, we can calculate d_oo, the distance between the two oxidizer orifices, and d_of, the distance from the middle oxidizer orifice to the fuel orifice, using simple trig. All numbers in the cell below are in inches and refer to distances on the bottom of the faceplate.

In [83]:
impinge_d = ((2*d_ox+d_fuel) / 3) * 5
d_oo = impinge_d * (np.tan(deg_to_rad(theta_nitrous_inner)) + np.tan(deg_to_rad(theta_nitrous_middle)))
d_of = impinge_d * (np.tan(deg_to_rad(theta_fuel)) + np.tan(deg_to_rad(theta_nitrous_middle)))
print("Distance between oxidizer orifices: ", d_oo)
print("Distance between middle oxidizer orifice and fuel orifice: ", d_of)
print("Impingement distance: ", impinge_d)

Distance between oxidizer orifices:  0.27008494499845
Distance between middle oxidizer orifice and fuel orifice:  0.6386172782550384
Impingement distance:  0.46875


We also want to calculate the height of the injector face. The literature states that the length of each orifice should be given by L/d = 3-10 (L = length of orifice, d = diameter of orifice). This design, will have an L/d ratio of 4 for the fuel orifice, and an L/d ratio of 5 for the oxidizer orifice. I am currently not sure if having different L/d ratios for the fuel and oxidizer orifices affects anything. 

With the lengths of the injector face for each orifice, we can calculate the necessary height of the faceplate using trig. We will get two similar heights (but different) heights from each oxidizer orifice, but we will use the average of the two. Numbers below are in inches.

In [69]:
L_ox = 5 * d_ox 
L_fuel = 4 * d_fuel
h_ox_inner = L_ox * np.cos(deg_to_rad(theta_nitrous_inner))
h_ox_middle = L_ox * np.cos(deg_to_rad(theta_nitrous_middle))
h_ox_avg = (h_ox_inner + h_ox_middle)/2
h_fuel = L_fuel * np.cos(deg_to_rad(theta_fuel))
print("Height of faceplate for oxidizer: ", h_ox_avg)
print("Height of faceplate for fuel: ", h_fuel)

Height of faceplate for oxidizer:  0.5252216656973887
Height of faceplate for fuel:  0.17366459261474934


Given the height of the faceplate, we now want to find the locations of the orifices on the top of the injector faceplate to further analyze if the spacing is feasible.

In [70]:
d_oo_top = (impinge_d + h_ox_avg) * np.tan(deg_to_rad(theta_nitrous_inner)) + (impinge_d + h_ox_avg) * np.tan(deg_to_rad(theta_nitrous_middle))
d_of_top = (impinge_d + h_fuel) * np.tan(deg_to_rad(theta_fuel)) - (impinge_d + h_fuel) * np.tan(deg_to_rad(theta_nitrous_middle))
print("Distance between oxidizer orifices on top: ", d_oo_top)
print("Distance between middle oxidizer orifice and fuel orifice on top: ", d_of_top)

Distance between oxidizer orifices on top:  0.5727078030077801
Distance between middle oxidizer orifice and fuel orifice on top:  0.45526451090115655


Next we will calculate the cross-sectional area of each of the fuel and oxidizer orifices using an equation derived from Bernoulli's principle and conservation of mass. Note here that we convert from square meters to square inches. (Later note: this does not work, we instead calculate areas from physical measurement). Next we get optimal cross-sectional area of each annulus, which is given by 4 * A_total. Not sure where this relation comes from. Finally, given we calculate the y dimension of the cross-section of each annulus given the x dimension.

Suggested widths: 0.3 in for fuel, 1.5 in for oxidizer.

In [72]:
# A_nitrous_total = ((mdot_nitrous_inner_total+mdot_nitrous_middle_total)/c_d) * np.sqrt(1/(2 * rho_nitrous * delta_pressure_injector)) * 1550 # Multiply these areas by 1550 to convert them from square meters to square inches 
# A_ethanol_total = (mdot_ethanol_total/c_d) * np.sqrt(1/(2 * rho_ethanol * delta_pressure_injector)) * 1550
A_nitrous_total = np.pi*(d_ox/2)**2 * 10
A_ethanol_total = np.pi*(d_fuel/2)**2 * 5
A_ox_annulus = A_nitrous_total * 4
A_fuel_annulus = A_ethanol_total * 4
d_ox_annulus_x = float(input("Enter in a value for the x-component of oxidizer annulus cross-sectional area. It should be bigger than the distance between the oxidizer holes, and also be wide enough to fit a 1/4th inch pipe fitting: "))
d_fuel_annulus_x = float(input("Enter in a value for the x-component of fuel annulus cross-sectional area. It should be wide enough to fit a 1/16th inch pipe fitting: "))
d_ox_annulus_y = A_ox_annulus / d_ox_annulus_x / 2
d_fuel_annulus_y = A_fuel_annulus / d_fuel_annulus_x / 2
print(f'X component of oxidizer annulus: {d_ox_annulus_x}')
print(f'Y component of oxidizer annulus: {d_ox_annulus_y}')
print(f'X component of fuel annulus: {d_fuel_annulus_x}')
print(f'Y component of fuel annulus: {d_fuel_annulus_y}')

Enter in a value for the x-component of oxidizer annulus cross-sectional area. It should be bigger than the distance between the oxidizer holes, and also be wide enough to fit a 1/4th inch pipe fitting: 0.77
Enter in a value for the x-component of fuel annulus cross-sectional area. It should be wide enough to fit a 1/16th inch pipe fitting: 0.3
X component of oxidizer annulus: 0.77
Y component of oxidizer annulus: 0.24404239807271563
X component of fuel annulus: 0.3
Y component of fuel annulus: 0.10226538585904275


Next we want to calculate the distance from each orifice to the impingement point, which will then allow us to calculate the time to impingement for each stream.

In [80]:
d_impingement_nitrous_inner = impinge_d / np.cos(deg_to_rad(theta_nitrous_inner))
d_impingement_nitrous_middle = impinge_d / np.cos(deg_to_rad(theta_nitrous_middle))
d_impingement_ethanol = impinge_d / np.cos(deg_to_rad(theta_fuel))

t_nitrous_inner = d_impingement_nitrous_inner / v_nitrous
t_nitrous_middle = d_impingement_nitrous_middle / v_nitrous
t_ethanol = d_impingement_ethanol / v_ethanol

The time for each stream to the impingement point cannot be the half period (or odd multiple of the half period) of the longitudinal mode of instability in the chamber (Huzel & Huang, pp. 148). The instability is dependent on the chamber length, so we can use this calculation to inform our decision on chamber length. We first need the speed of sound, which is given by sqrt(gamma*R*Tc/M), which are all known parameters. We then calculate the frequency of instability modes, which is the speed of sound over twice the chamber length. After some algebra, we find that the chamber length should not be the numbers given below (or any odd multiple).

In [82]:
# Known engine parameters, SI units
gamma = 1.1589
R = 324.0271
Tc = 3028

# speed of sound in chamber
a_c = np.sqrt(gamma*R*Tc)

# chamber lengths to avoid, in
L_avoid_1 = a_c * t_nitrous_inner / 4 * 39.3701
L_avoid_2 = a_c * t_nitrous_middle / 4 * 39.3701
L_avoid_3 = a_c * t_ethanol / 4 * 39.3701
print(f"Avoid these lengths and odd multiples: {L_avoid_1}, {L_avoid_2}, {L_avoid_3}")

Avoid these lengths and odd multiples: 125.307856382723, 127.91558849187926, 172.004028762347
